In [1]:
# Import packages

import pandas as pd
import numpy as np

In [2]:
import altair as alt
from altair_saver import save

In [3]:
# Tools

import functools
def conjunction(*conditions):
    return functools.reduce(np.logical_and, conditions)

In [4]:
%%html
    <style>
        @import url('https://fonts.googleapis.com/css?family=Encode+Sans:400');
        @import url('https://fonts.googleapis.com/css?family=Open+Sans:400');
        @import url('https://fonts.googleapis.com/css?family=Open+Sans:700');
    </style>

In [5]:
def catalyst(*args, **kwargs):
    font = "Open Sans"
    labelFont = "Open Sans" 
    sourceFont = "Open Sans"
    # Axes
    axisColor = "#000000"
    gridColor = "#DEDDDD"
    # Colors
    main_palette = ["#2980B9", "#003366", "#FFAE19", "#FF4500", "#438B28", "#45B39D", "#99ADC1", "#212F3C"]
    return {
        "width": 800, 
        "height": 400, 
        "config": {
            "title": {
                "fontSize": 18,
                "font": font,
                "anchor": "center",
                "fontColor": "#000000",
            },
            "axisX": {
                "domain": True,
                "domainColor": axisColor,
                #"domainWidth": 1,
                "grid": False,
                "labelFont": labelFont,
                "labelFontSize": 13,
                #"labelAngle": 0,
                #"tickColor": axisColor,
                #"tickSize": 5, 
                "titleFont": font,
                "titleFontSize": 13,
                "titleFontWeight": "normal",
                #"titlePadding": 10, 
                "title": "X Axis Title (units)", 
                "labelAngle": -45,
                #"titleAngle":0
            },
            "axisY": {
                "domain": True,
                "grid": False,
                "gridColor": gridColor,
                "gridWidth": 1,
                "labelFont": labelFont,
                "labelFontSize": 13,
                "labelAngle": 0,
                "ticks": False, 
                "titleFont": font,
                "titleFontSize": 13,
                "titleFontWeight": "normal",
                "titlePadding": 10, 
                "title": "Y Axis Title (units)",
                #"titleY": -10, 
                #"titleX": 18,
                #"titleAngle": 0 #-90
            },
            "range": {
                "category": main_palette
            },
            "legend": {
                "labelFont": labelFont,
                "labelFontSize": 13,
                "symbolType": "square", 
                "symbolSize": 100, 
                "titleFont": font,
                "titleFontSize": 13,
                "titleFontWeight": "normal",
                "title": "Legend", 
                "orient": "right", 
                "offset": 0, 
                "labelLimit": 0
            },
            "tooltip":{
                "font": "Open Sans"
            },
            "view": {
                "stroke": "transparent", 
        ### MARKS CONFIGURATIONS ###
           "text": {
               "font": "Open Sans",
               "color": main_palette,
               "fontSize": 13,
               "align": "right",
               "fontWeight": 400,
               "size": 13,
           }, 
           "bar": {
                "size": 40,
                "binSpacing": 1,
                "continuousBandSize": 30,
                "discreteBandSize": 30,
                "fill": main_palette,
                "stroke": False,
           },
            }
        }
    }

In [6]:
alt.themes.register('catalyst', catalyst)
alt.themes.enable('catalyst');

In [112]:
# Load Nigeria MTF Data: Finance Details
#Total number of households surveyed in the overall survey: 3,668

chunksize = 10

mtf_list = []
chunksize = 10
for chunk in pd.read_csv("../../data/nigeria_finance.csv", encoding='latin-1', chunksize = chunksize):
    mtf_list.append(chunk)
    
finance = pd.concat(mtf_list, axis=0)
finance = pd.DataFrame(data = finance)

In [113]:
# Load Nigeria MTF Data: Cooking Details, cooking['i19a'] is primary cooking fuel

chunksize = 10

mtf_list = []
chunksize = 10
for chunk in pd.read_csv("../../data/nigeria_cooking.csv", encoding='latin-1', chunksize = chunksize):
    mtf_list.append(chunk)
    
cooking = pd.concat(mtf_list, axis=0)
cooking = pd.DataFrame(data = cooking)

In [114]:
# Load Nigeria MTF Data: Willingness to Pay Solar Details

chunksize = 10

mtf_list = []
chunksize = 10
for chunk in pd.read_csv("../../data/nigeria_wtp_solar.csv", encoding='latin-1', chunksize = chunksize):
    mtf_list.append(chunk)
    
wtp_solar = pd.concat(mtf_list, axis=0)
wtp_solar = pd.DataFrame(data = wtp_solar)
wtp_solar['e_amount_str'] = wtp_solar['e_amount'].astype('str')
wtp_solar['i19a'] = finance['i19a']
# e_3 is pay upfront
# e_4 is pay if given 6 months to make payment
# e_5 is pay if given 12 months to make payment
# e_6 is pay if given 24 months to make payment

In [115]:
# Grid access
chunksize = 10

mtf_list = []
chunksize = 10
for chunk in pd.read_csv("../../data/nigeria_grid_access.csv", encoding='latin-1', chunksize = chunksize):
    mtf_list.append(chunk)
    
grid_access = pd.concat(mtf_list, axis=0)
grid_access = pd.DataFrame(data = grid_access)
wtp_solar['c2'] = grid_access['c2']

In [116]:
# Prepare Cooking data for dropdown menus
# cooking has different number of rows compared to other dataframes and has some repeated households
# Primary stove is composite variable due to how questions were asked in survey
# i19a is primary cooking fuel
cooking['primary_stove'] = cooking[cooking['i35'] == 'Yes']['i3'] # Creates primary cooking stove feature
cooking_drop = cooking[['hh_id', 'primary_stove']].drop_duplicates(subset=['hh_id']) # Drop duplicates since some hh's that have multiple observations
cooking_drop['primary_stove'].fillna('Missing Data', inplace=True) # Some hh's missing primary stove data
wtp_solar = wtp_solar.merge(cooking_drop, how='left', on='hh_id') # Add primary stove to grid_ext
#grid_access = grid_access.merge(cooking_drop, how='left', on='hh_id') # Add primary stove to grid_access
#tier_data = tier_data.merge(cooking_drop, how='left', on='hh_id') # Add primary stove to tier_data

In [128]:
# Willingness to pay upfront for solar device

alt.data_transformers.disable_max_rows()
source = wtp_solar[wtp_solar[['e_amount']].notnull().all(1)]

chart = alt.Chart(source).transform_joinaggregate(
    total = 'count()'
).transform_calculate(
    pct  = '1 / datum.total'
).mark_bar().encode(
    x=alt.X('e_amount:N', axis = alt.Axis(title = 'Nigerian Naira')),
    y=alt.Y('sum(pct):Q', stack='normalize', axis = alt.Axis(title = '', format = '.0%')),
    color='e_3'
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["Would you be willing to pay ₦ ___ upfront for a solar home system?"],
      "color": "black",
      "subtitleColor": "black",
      "offset": 40 # Offsets title 50 px up from original position
    }
)
# text = alt.Chart(source).transform_joinaggregate(
#     total = 'count(*)'
# ).transform_calculate(
#     pct  = '1 / datum.total'
# ).mark_text(color='white').encode(
#     x=alt.X('e_amount:N'),
#     y=alt.Y('sum(pct):Q', stack='normalize', axis = alt.Axis(title = '', format = '.0%')),
#     detail='e_3',
#     text=alt.Text('sum(pct):Q', format='.2f')
# )

# FILTERS
# Locality Filter
locality_options = [None, 0, 1]
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
     options= locality_options, 
     labels = locality_labels, 
     name = "Locality Breakdown  ")
locality_select=alt.selection_single(
     fields=['locality'],
     bind=locality_dropdown)

# National Grid Connection Filter
connection = [None, 'Yes', 'No']
connection_labels = ['All Responses', 'Yes', 'No']
connection_dropdown=alt.binding_select(options=connection, 
                                 labels = connection_labels, 
                                 name = "Is the household connected to the national grid?  ")
connection_select=alt.selection_single(fields=['c2'],
                                bind=connection_dropdown)

# Primary Stove Filter
stoves = [None, '3-Stone/Open Fire Stove', 'Koresone Stove', 'Missing Data',
       'Manufactured Stove Traditional', 'LPG/Natural Gas Stove',
       'Electric Stove']
stove_labels = ['All Responses', '3-Stone/Open Fire Stove', 'Kerosene Stove', 'Primary Stove Not Listed',
       'Manufactured Stove Traditional', 'LPG/Natural Gas Stove',
       'Electric Stove']
stove_dropdown=alt.binding_select(options=stoves, 
                                 labels = stove_labels, 
                                 name = "Primary Stove  ")
stove_select=alt.selection_single(fields=['primary_stove'],
                                bind=stove_dropdown)

# Cooking Fuel Filter
fuels = [None, 'Wood purchased', 'Wood collected', 'Crop Residue/Plant Biomass',
       'Kerosene', 'Charcoal', 'LPG/cooking gas', 'Electric',
       'Charcoal Briquettes', 'Garbage', 'Piped Natural Gas',
       'Coal Briquette', 'Biomass Briquette', 'Other, specify',
       'Coal/lignite']
fuel_labels = ['All Responses', 'Wood purchased', 'Wood collected', 'Crop Residue/Plant Biomass',
       'Kerosene', 'Charcoal', 'LPG/cooking gas', 'Electric',
       'Charcoal Briquettes', 'Garbage', 'Piped Natural Gas',
       'Coal Briquette', 'Biomass Briquette', 'Other',
       'Coal/lignite']
fuel_dropdown=alt.binding_select(options=fuels, 
                                 labels = fuel_labels, 
                                 name = "Primary Source of Cooking Fuel  ")
fuel_select=alt.selection_single(fields=['i19a'],
                                bind=fuel_dropdown)

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['e_3']].notnull().all(1)]['hh_id'])) /
            3668 * 100, 2) # change variable

chart = chart.add_selection(
    fuel_select
).transform_filter(
    fuel_select 
).add_selection(
    stove_select
).transform_filter(
    stove_select 
).add_selection(
    connection_select
).transform_filter(
    connection_select 
).add_selection(
     locality_select
).transform_filter(
     locality_select
)

final = alt.concat(chart,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (n = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).',
         '₦2970 - ₦9000 for low capacity solar home system that can power multiple lightbulbs and supports mobile charging.',
         '₦33000 - ₦100000 for high capacity solar home system with ability to power a television.'],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
).configure_axisX(
    labelAngle = 0
)

final

alt.ConcatChart(...)

In [124]:
# Save as an HTML file
#final.save('wtp_solar_upfront.html')

# Save as a JSON file
#final.save('wtp_solar_upfront.json')

In [132]:
# Willingness to pay over 12 months for solar device

alt.data_transformers.disable_max_rows()
source = wtp_solar[wtp_solar[['e_5']].notnull().all(1)]

chart = alt.Chart(source).transform_joinaggregate(
    total = 'count()'
).transform_calculate(
    pct  = '1 / datum.total'
).mark_bar().encode(
    x=alt.X('e_amount:N', axis = alt.Axis(title = 'Nigerian Naira')),
    y=alt.Y('sum(pct):Q', stack='normalize', axis = alt.Axis(title = '', format = '.0%')),
    color='e_5'
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["Would you be willing to pay ₦ ___ over 12 months for a solar home system?"],
      "color": "black",
      "subtitleColor": "black",
      "offset": 40 # Offsets title 50 px up from original position
    }
)
# text = alt.Chart(source).transform_joinaggregate(
#     total = 'count(*)'
# ).transform_calculate(
#     pct  = '1 / datum.total'
# ).mark_text(color='white').encode(
#     x=alt.X('e_amount:N'),
#     y=alt.Y('sum(pct):Q', stack='normalize', axis = alt.Axis(title = '', format = '.0%')),
#     detail='e_3',
#     text=alt.Text('sum(pct):Q', format='.2f')
# )

# FILTERS
# Locality Filter
locality_options = [None, 0, 1]
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
     options= locality_options, 
     labels = locality_labels, 
     name = "Locality Breakdown  ")
locality_select=alt.selection_single(
     fields=['locality'],
     bind=locality_dropdown)

# National Grid Connection Filter
connection = [None, 'Yes', 'No']
connection_labels = ['All Responses', 'Yes', 'No']
connection_dropdown=alt.binding_select(options=connection, 
                                 labels = connection_labels, 
                                 name = "Is the household connected to the national grid?  ")
connection_select=alt.selection_single(fields=['c2'],
                                bind=connection_dropdown)

# Primary Stove Filter
stoves = [None, '3-Stone/Open Fire Stove', 'Koresone Stove', 'Missing Data',
       'Manufactured Stove Traditional', 'LPG/Natural Gas Stove',
       'Electric Stove']
stove_labels = ['All Responses', '3-Stone/Open Fire Stove', 'Kerosene Stove', 'Primary Stove Not Listed',
       'Manufactured Stove Traditional', 'LPG/Natural Gas Stove',
       'Electric Stove']
stove_dropdown=alt.binding_select(options=stoves, 
                                 labels = stove_labels, 
                                 name = "Primary Stove  ")
stove_select=alt.selection_single(fields=['primary_stove'],
                                bind=stove_dropdown)

# Cooking Fuel Filter
fuels = [None, 'Wood purchased', 'Wood collected', 'Crop Residue/Plant Biomass',
       'Kerosene', 'Charcoal', 'LPG/cooking gas', 'Electric',
       'Charcoal Briquettes', 'Garbage', 'Piped Natural Gas',
       'Coal Briquette', 'Biomass Briquette', 'Other, specify',
       'Coal/lignite']
fuel_labels = ['All Responses', 'Wood purchased', 'Wood collected', 'Crop Residue/Plant Biomass',
       'Kerosene', 'Charcoal', 'LPG/cooking gas', 'Electric',
       'Charcoal Briquettes', 'Garbage', 'Piped Natural Gas',
       'Coal Briquette', 'Biomass Briquette', 'Other',
       'Coal/lignite']
fuel_dropdown=alt.binding_select(options=fuels, 
                                 labels = fuel_labels, 
                                 name = "Primary Source of Cooking Fuel  ")
fuel_select=alt.selection_single(fields=['i19a'],
                                bind=fuel_dropdown)

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['e_5']].notnull().all(1)]['hh_id'])) /
            3668 * 100, 2) # change variable

chart = chart.add_selection(
    fuel_select
).transform_filter(
    fuel_select 
).add_selection(
    stove_select
).transform_filter(
    stove_select 
).add_selection(
    connection_select
).transform_filter(
    connection_select 
).add_selection(
     locality_select
).transform_filter(
     locality_select
)

final = alt.concat(chart,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (n = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).',
         '₦2970 - ₦9000 for low capacity solar home system that can power multiple lightbulbs and supports mobile charging.',
         '₦33000 - ₦100000 for high capacity solar home system with ability to power a television.'],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
).configure_axisX(
    labelAngle = 0
)

final

alt.ConcatChart(...)

In [131]:
# Save as an HTML file
#final.save('wtp_solar_12_months.html')

# Save as a JSON file
#final.save('wtp_solar_12_months.json')

In [136]:
for i in range(wtp_solar.shape[0]):
    if wtp_solar['e_3b'][i] == 'Other, specify':
        wtp_solar['e_3b'][i] = 'Other'

/var/folders/0t/klm_ph4n3yxcbm49ppf1c5f40000gn/T/ipykernel_2061/2316971183.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  wtp_solar['e_3b'][i] = 'Other'


In [152]:
# Why not accept offer for solar device upfront?

# Data source
alt.data_transformers.disable_max_rows()
source = wtp_solar[wtp_solar[['e_3b']].notnull().all(1)] # Change your variables here

col1 = source['elc_aggr_tier'] != 'NaN'
col2 = source['e_3b'] != 'NaN' # Change variables here

source = source[conjunction(col1,col2)]
df = source[['hh_id', 'elc_aggr_tier', 'locality', 'e_3b', 'primary_stove', 'i19a']] # Change variables here

# Draw the chart 
chart = alt.Chart(df).transform_joinaggregate(
    total = 'count(*)'
).transform_calculate(
    pct = '1 / datum.total'
).encode(
    x = alt.X('e_3b', # Change variable
              sort=alt.EncodingSortField(field='e_3b', # Change variable 
                                         op="count", 
                                         order='descending'),
              axis = alt.Axis(title = " ")),
    y = alt.Y('sum(pct):Q', axis = alt.Axis(title = '', format = '%')),
    color = 'e_3b:N',
    tooltip = 'e_3b' # Change variable
).properties(
    height = 400,
    width = 500
)

# Locality Filter
locality_options = [None, 0, 1]
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
     options= locality_options, 
     labels = locality_labels, 
     name = "Locality Breakdown  ")
locality_select=alt.selection_single(
     fields=['locality'],
     bind=locality_dropdown)

# Tier Filter
tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, 
                                 labels = tier_labels, 
                                 name = "Electricity Tiers  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# Primary Stove Filter
stoves = [None, '3-Stone/Open Fire Stove', 'Koresone Stove', 'Missing Data',
       'Manufactured Stove Traditional', 'LPG/Natural Gas Stove',
       'Electric Stove']
stove_labels = ['All Responses', '3-Stone/Open Fire Stove', 'Kerosene Stove', 'Primary Stove Not Listed',
       'Manufactured Stove Traditional', 'LPG/Natural Gas Stove',
       'Electric Stove']
stove_dropdown=alt.binding_select(options=stoves, 
                                 labels = stove_labels, 
                                 name = "Primary Stove  ")
stove_select=alt.selection_single(fields=['primary_stove'],
                                bind=stove_dropdown)

# Cooking Fuel Filter
fuels = [None, 'Wood purchased', 'Wood collected', 'Crop Residue/Plant Biomass',
       'Kerosene', 'Charcoal', 'LPG/cooking gas', 'Electric',
       'Charcoal Briquettes', 'Garbage', 'Piped Natural Gas',
       'Coal Briquette', 'Biomass Briquette', 'Other, specify',
       'Coal/lignite']
fuel_labels = ['All Responses', 'Wood purchased', 'Wood collected', 'Crop Residue/Plant Biomass',
       'Kerosene', 'Charcoal', 'LPG/cooking gas', 'Electric',
       'Charcoal Briquettes', 'Garbage', 'Piped Natural Gas',
       'Coal Briquette', 'Biomass Briquette', 'Other',
       'Coal/lignite']
fuel_dropdown=alt.binding_select(options=fuels, 
                                 labels = fuel_labels, 
                                 name = "Primary Source of Cooking Fuel  ")
fuel_select=alt.selection_single(fields=['i19a'],
                                bind=fuel_dropdown)

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['e_3b']].notnull().all(1)]['hh_id'])) /
            3668 * 100, 2) # change variable

# Final Chart with bells and whistles
final = (chart.mark_bar() + chart.mark_text( # This blue is from the AIP site.
    align = 'center', 
    baseline='bottom'
).encode(
    text = alt.Text('sum(pct):Q', 
                    format = '.2%'))
 ).add_selection(
    fuel_select
).transform_filter(
    fuel_select 
).add_selection(
    stove_select
).transform_filter(
    stove_select 
).add_selection(
     locality_select
 ).transform_filter(
     locality_select
).add_selection(
    tier_select
).transform_filter(
    tier_select 
).properties(
    title={
      "text": ["Why would you not accept the offer to pay", "upfront for the solar home system?"], 
   #   "subtitle": ["You are viewing XX% of responses from the Nigeria Multi-Tiered Framework Survey.", " "],
      "color": "black",
      "subtitleColor": "black", 
        "offset": 40
    }
)

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (n = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).'],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
).configure_axisX(
    labelAngle = 45
)
final

alt.ConcatChart(...)

In [153]:
# Save as an HTML file
#final.save('wtp_solar_upfront_reason.html')

# Save as a JSON file
#final.save('wtp_solar_upfront_reason.json')

In [ ]:
for i in range(wtp_solar.shape[0]):
    if wtp_solar['e_5b'][i] == 'Other, specify':
        wtp_solar['e_5b'][i] = 'Other'

In [147]:
# Reasons not paying for solar device over 12 months

# Data source
alt.data_transformers.disable_max_rows()
source = wtp_solar[wtp_solar[['e_5b']].notnull().all(1)] # Change your variables here

col1 = source['elc_aggr_tier'] != 'NaN'
col2 = source['e_5b'] != 'NaN' # Change variables here

source = source[conjunction(col1,col2)]
df = source[['hh_id', 'elc_aggr_tier', 'locality', 'e_5b']] # Change variables here

# Draw the chart 
chart = alt.Chart(df).transform_joinaggregate(
    total = 'count(*)'
).transform_calculate(
    pct = '1 / datum.total'
).encode(
    x = alt.X('e_5b', # Change variable
              sort=alt.EncodingSortField(field='e_5b', # Change variable 
                                         op="count", 
                                         order='descending'),
              axis = alt.Axis(title = " ")),
    y = alt.Y('sum(pct):Q', axis = alt.Axis(title = '', format = '%')),
    color = 'e_5b:N',
    tooltip = 'e_5b' # Change variable
).properties(
    height = 400,
    width = 500
)

# Locality Filter
locality_options = [None, 0, 1]
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
     options= locality_options, 
     labels = locality_labels, 
     name = "Locality Breakdown  ")
locality_select=alt.selection_single(
     fields=['locality'],
     bind=locality_dropdown)

# Tier Filter
tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, 
                                 labels = tier_labels, 
                                 name = "Electricity Tiers  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# Primary Stove Filter
stoves = [None, '3-Stone/Open Fire Stove', 'Koresone Stove', 'Missing Data',
       'Manufactured Stove Traditional', 'LPG/Natural Gas Stove',
       'Electric Stove']
stove_labels = ['All Responses', '3-Stone/Open Fire Stove', 'Kerosene Stove', 'Primary Stove Not Listed',
       'Manufactured Stove Traditional', 'LPG/Natural Gas Stove',
       'Electric Stove']
stove_dropdown=alt.binding_select(options=stoves, 
                                 labels = stove_labels, 
                                 name = "Primary Stove  ")
stove_select=alt.selection_single(fields=['primary_stove'],
                                bind=stove_dropdown)

# Cooking Fuel Filter
fuels = [None, 'Wood purchased', 'Wood collected', 'Crop Residue/Plant Biomass',
       'Kerosene', 'Charcoal', 'LPG/cooking gas', 'Electric',
       'Charcoal Briquettes', 'Garbage', 'Piped Natural Gas',
       'Coal Briquette', 'Biomass Briquette', 'Other, specify',
       'Coal/lignite']
fuel_labels = ['All Responses', 'Wood purchased', 'Wood collected', 'Crop Residue/Plant Biomass',
       'Kerosene', 'Charcoal', 'LPG/cooking gas', 'Electric',
       'Charcoal Briquettes', 'Garbage', 'Piped Natural Gas',
       'Coal Briquette', 'Biomass Briquette', 'Other',
       'Coal/lignite']
fuel_dropdown=alt.binding_select(options=fuels, 
                                 labels = fuel_labels, 
                                 name = "Primary Source of Cooking Fuel  ")
fuel_select=alt.selection_single(fields=['i19a'],
                                bind=fuel_dropdown)

# Percentage of responses shown in the chart
pct = df.shape[0] / wtp_solar.shape[0]

# Final Chart with bells and whistles
final = (chart.mark_bar() + chart.mark_text( # This blue is from the AIP site.
    align = 'center', 
    baseline='bottom'
).encode(
    text = alt.Text('sum(pct):Q', 
                    format = '.2%'))
 ).add_selection(
    fuel_select
).transform_filter(
    fuel_select 
).add_selection(
    stove_select
).transform_filter(
    stove_select 
).add_selection(
     locality_select
 ).transform_filter(
     locality_select
).add_selection(
    tier_select
).transform_filter(
    tier_select 
).properties(
    title={
      "text": ["Why would you not accept the offer to pay for",  "the solar home system within 12 months?"], 
   #   "subtitle": ["You are viewing XX% of responses from the Nigeria Multi-Tiered Framework Survey.", " "],
      "color": "black",
      "subtitleColor": "black",
        "offset": 40
    }
)
# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['e_5b']].notnull().all(1)]['hh_id'])) /
            3668 * 100, 2) # change variable

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (n = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).'],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
).configure_axisX(
    labelAngle = 45
)
final

alt.ConcatChart(...)

In [148]:
# Save as an HTML file
#final.save('wtp_solar_12m_reason.html')

# Save as a JSON file
#final.save('wtp_solar_12m_reason.json')

In [142]:
# Willingness to pay for solar device over 12 months (old)

# Data source
alt.data_transformers.disable_max_rows()
source = wtp_solar[wtp_solar[['e_5']].notnull().all(1)] # Change your variables here

col1 = source['elc_aggr_tier'] != 'NaN'
col2 = source['e_5'] != 'NaN' # Change variables here

source = source[conjunction(col1,col2)]
df = source[['hh_id', 'elc_aggr_tier', 'locality', 'e_5']] # Change variables here

# Draw the chart 
chart = alt.Chart(df).transform_joinaggregate(
    total = 'count(*)'
).transform_calculate(
    pct = '1 / datum.total'
).encode(
    x = alt.X('e_5', # Change variable
              sort=alt.EncodingSortField(field='e_5', # Change variable 
                                         op="count", 
                                         order='descending'),
              axis = alt.Axis(title = " ")),
    y = alt.Y('sum(pct):Q', axis = alt.Axis(title = '', format = '%')),
    color = alt.Color('e_5:N', legend = None),
    tooltip = 'e_5' # Change variable
).properties(
    height = 400,
    width = 500
)

# Locality Filter
locality_options = [None, 0, 1]
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
     options= locality_options, 
     labels = locality_labels, 
     name = "Locality Breakdown  ")
locality_select=alt.selection_single(
     fields=['locality'],
     bind=locality_dropdown)

# Tier Filter
tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, 
                                 labels = tier_labels, 
                                 name = "Tiers  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# Percentage of responses shown in the chart
pct = df.shape[0] / wtp_solar.shape[0]

# Final Chart with bells and whistles
final = (chart.mark_bar() + chart.mark_text( # This blue is from the AIP site.
    align = 'center', 
    baseline='bottom'
).encode(
    text = alt.Text('sum(pct):Q', 
                    format = '.2%'))
 ).add_selection(
     locality_select
 ).transform_filter(
     locality_select
).add_selection(
    tier_select
).transform_filter(
    tier_select 
).properties(
    title={
      "text": ["At a given price between $2000 and $1000, would you be willing" , 
               "to pay\nfor a solar device if you had 12 months to pay for it?"], 
   #   "subtitle": ["You are viewing XX% of responses from the Nigeria Multi-Tiered Framework Survey.", " "],
      "color": "black",
      "subtitleColor": "black",
        "offset": 40
    }
)

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['e_5']].notnull().all(1)]['hh_id'])) /
            3668 * 100, 2) # change variable

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (n = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).'],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
).configure_axisX(
    labelAngle = 45
)

final

alt.ConcatChart(...)

In [ ]:
# Save as an HTML file
#final.save('wtp_solar_12_months.html')

# Save as a JSON file
#final.save('wtp_solar_12_months.json')

In [146]:
# Willingness to pay for solar device (old)

# Data source
alt.data_transformers.disable_max_rows()
source = wtp_solar[wtp_solar[['e_3']].notnull().all(1)] # Change your variables here

col1 = source['elc_aggr_tier'] != 'NaN'
col2 = source['e_3'] != 'NaN' # Change variables here

source = source[conjunction(col1,col2)]
df = source[['hh_id', 'elc_aggr_tier', 'locality', 'e_3']] # Change variables here

# Draw the chart 
chart = alt.Chart(df).transform_joinaggregate(
    total = 'count(*)'
).transform_calculate(
    pct = '1 / datum.total'
).encode(
    x = alt.X('e_3', # Change variable
              sort=alt.EncodingSortField(field='e_3', # Change variable 
                                         op="count", 
                                         order='descending'),
              axis = alt.Axis(title = " ")),
    y = alt.Y('sum(pct):Q', axis = alt.Axis(title = '', format = '%')),
    color = alt.Color('e_3:N', legend = None),
    tooltip = 'e_3' # Change variable
).properties(
    height = 400,
    width = 500
)

# Locality Filter
locality_options = [None, 0, 1]
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
     options= locality_options, 
     labels = locality_labels, 
     name = "Locality Breakdown  ")
locality_select=alt.selection_single(
     fields=['locality'],
     bind=locality_dropdown)

# Tier Filter
tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, 
                                 labels = tier_labels, 
                                 name = "Electricity Tiers  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['e_3']].notnull().all(1)]['hh_id'])) /
            3668 * 100, 2) # change variable

# Final Chart with bells and whistles
final = (chart.mark_bar() + chart.mark_text( # This blue is from the AIP site.
    align = 'center', 
    baseline='bottom'
).encode(
    text = alt.Text('sum(pct):Q', 
                    format = '.2%'))
 ).add_selection(
     locality_select
 ).transform_filter(
     locality_select
).add_selection(
    tier_select
).transform_filter(
    tier_select 
).properties(
    title={
      "text": ["At a given price between $2000 and $1000, would you", "be willing to pay upfront for a solar device?"], 
   #   "subtitle": ["You are viewing XX% of responses from the Nigeria Multi-Tiered Framework Survey.", " "],
      "color": "black",
      "subtitleColor": "black",
        "offset": 40
    }
)
final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (n = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).'],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
).configure_axisX(
    labelAngle = 45
)

final

final

alt.ConcatChart(...)

In [10]:
# Bar Chart Example
# B.14 from the Kenya MTF: What is your household’s main source of drinking water?

# Data source
alt.data_transformers.disable_max_rows()
source = module[module[['b_b_14']].notnull().all(1)] # Change your variables here

col1 = source['elc_aggr_tier'] != 'NaN'
col2 = source['b_b_14'] != 'NaN' # Change variables here

source = source[conjunction(col1,col2)]
df = source[['elc_aggr_tier', 'locality_ur', 'b_b_14']] # Change variables here

# Draw the chart 
chart = alt.Chart(df).transform_joinaggregate(
    total = 'count(*)'
).transform_calculate(
    pct = '1 / datum.total'
).encode(
    x = alt.X('b_b_14', # Change variable
              sort=alt.EncodingSortField(field="b_b_14", # Change variable 
                                         op="count", 
                                         order='descending'),
              axis = alt.Axis(title = " ")),
    y = alt.Y('sum(pct):Q', axis = alt.Axis(title = '', format = '%')),
    tooltip = 'b_b_14' # Change variable
).properties(
    height = 400,
    width = 500
)

# Locality Filter
locality_options = [None, 'Urban', 'Rural']
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality_ur'],
    bind=locality_dropdown)

# Tier Filter
tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, 
                                 labels = tier_labels, 
                                 name = "Tiers  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# Percentage of responses shown in the chart
pct = df.shape[0] / module.shape[0]

# Final Chart with bells and whistles
final = (chart.mark_bar(color = '#304ca2') + chart.mark_text( # This blue is from the AIP site.
    align = 'center', 
    baseline='bottom'
).encode(
    text = alt.Text('sum(pct):Q', 
                    format = '.2%'))
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    tier_select
).transform_filter(
    tier_select 
).properties(
    title={
      "text": ["Example Bar Chart (YOUR TITLE HERE)"], 
      "subtitle": ["You are viewing XX% of responses from the Nigeria Multi-Tiered Framework Survey.", " "],
      "color": "black",
      "subtitleColor": "black"
    }
)

final

NameError: name 'module' is not defined

In [ ]:
# Histogram Example
# How many solar-powered systems do you have?

# Data Source
alt.data_transformers.disable_max_rows()
source = solar[solar[['sum_solar']].notnull().all(1)]

col1 = source['sum_solar'] # != 'NaN'
col2 = source['elc_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['elc_aggr_tier','sum_solar', 'locality']]

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar(color = '#304ca2'
).encode(
    alt.X("sum_solar:Q", 
          bin=alt.Bin(extent=[1, 15], step=1), # Change the step to adjust bin size
          scale = alt.Scale(domain=(1,15),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Response")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = "Percent"),
    tooltip = [alt.Tooltip('b_b_9:N', title = "Response (Binned)"), 
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    tier_select
).transform_filter(
    tier_select 
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["How many solar-powered systems do you own?"], 
      "subtitle": ["You are viewing 1% of responses from the Nigeria Multi-Tiered Framework Survey.", " "],
      "color": "black",
      "subtitleColor": "black"
    }
)

final

In [ ]:
# Primary vs Secondary Cooking Fuel Sources

# Data
alt.data_transformers.disable_max_rows()
source = cooking[cooking[['i19a', 'i19b']].notnull().all(1)]

col1 = source['i19a'] != 'NaN'
col2 = source['elc_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['elc_aggr_tier','i19a', 'i19b', 'locality']]

# Configure common options
base = alt.Chart(df).transform_aggregate(
    chart_count='count()',
    groupby=['i19a', 'i19b']
).encode(
    alt.X('i19a:O', 
          scale=alt.Scale(paddingInner=0), 
          title = "Primary Fuel"),
    alt.Y('i19b:O', 
          scale=alt.Scale(paddingInner=0), 
          title = "Secondary Fuel"),
)

# Configure heatmap
heatmap = base.mark_rect().encode(
    color=alt.Color('chart_count:Q',
        scale=alt.Scale(scheme='blues'),
        legend=None
    )
)

# Configure text
text = base.mark_text(baseline='middle'
).transform_joinaggregate(
    count = 'count(chart_count)',
    groupby = ['i19a', 'i19b']
).transform_calculate(
    pct = alt.datum.chart_count / df.shape[0]
).encode(
    text=alt.Text('pct:Q', format = '.2%'),
    color=alt.condition(
        alt.datum.chart_count < 300, # Change the color of the text here
        alt.value('black'),
        alt.value('white')
    )
)

# Locality Filter
locality_options = [None, 0, 1]
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality'],
    bind=locality_dropdown)

# Tier Filter
tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, labels = tier_labels, name = "Tiers  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# Roof filter
#roofs = [None, 'Corrugated iron sheet', 'Concrete/Cement', 'Thatch', 'Wood and mud', 'Bamboo/Reed', 
 #        'Plastic canvas', 'Asbestos', 'Bricks']
#roof_labels = ['All roof types', 'Corrugated iron sheet', 'Concrete/Cement', 'Thatch', 'Wood and mud', 'Bamboo/Reed', 
 #        'Plastic canvas', 'Asbestos', 'Bricks']
#roof_dropdown=alt.binding_select(options=roofs, labels = roof_labels, name = "Roofs  ")
#roof_select=alt.selection_single(fields=['b_b_11'],
 #                               bind=roof_dropdown)

# Draw the chart
final = (heatmap + text).properties(
    height = 300,
    width = 800
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    tier_select
).transform_filter(
    tier_select 
# ).add_selection(
#     roof_select
# ).transform_filter(
#     roof_select
).properties(
    title={
      "text": ['What top two cooking fuels do you use in a year?'], 
    #  "subtitle": ["You are viewing XX% of responses from the Kenya Multi-Tiered Framework Survey.", " "],
      "color": "black",
      "subtitleColor": "black"
    }
)

final

In [ ]:
# Primary vs Secondary Cooking Fuel Sources

# Data
alt.data_transformers.disable_max_rows()
source = cooking[cooking[['i19a', 'primary_stove']].notnull().all(1)]

col1 = source['i19a'] != 'NaN'
col2 = source['elc_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['elc_aggr_tier','i19a', 'primary_stove', 'locality']]

# Configure common options
base = alt.Chart(df).transform_aggregate(
    chart_count='count()',
    groupby=['i19a', 'primary_stove']
).encode(
    alt.X('i19a:O', 
          scale=alt.Scale(paddingInner=0), 
          title = "Primary Cooking Fuel"),
    alt.Y('primary_stove:O', 
          scale=alt.Scale(paddingInner=0), 
          title = "Primary Cooking Stove"),
)

# Configure heatmap
heatmap = base.mark_rect().encode(
    color=alt.Color('chart_count:Q',
        scale=alt.Scale(scheme='blues'),
        legend=None
    )
)

# Configure text
text = base.mark_text(baseline='middle'
).transform_joinaggregate(
    count = 'count(chart_count)',
    groupby = ['i19a', 'primary_stove']
).transform_calculate(
    pct = alt.datum.chart_count / df.shape[0]
).encode(
    text=alt.Text('pct:Q', format = '.2%'),
    color=alt.condition(
        alt.datum.chart_count < 300, # Change the color of the text here
        alt.value('black'),
        alt.value('white')
    )
)

# Locality Filter
locality_options = [None, 0, 1]
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality'],
    bind=locality_dropdown)

# Tier Filter
tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, labels = tier_labels, name = "Tiers  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# Roof filter
#roofs = [None, 'Corrugated iron sheet', 'Concrete/Cement', 'Thatch', 'Wood and mud', 'Bamboo/Reed', 
 #        'Plastic canvas', 'Asbestos', 'Bricks']
#roof_labels = ['All roof types', 'Corrugated iron sheet', 'Concrete/Cement', 'Thatch', 'Wood and mud', 'Bamboo/Reed', 
 #        'Plastic canvas', 'Asbestos', 'Bricks']
#roof_dropdown=alt.binding_select(options=roofs, labels = roof_labels, name = "Roofs  ")
#roof_select=alt.selection_single(fields=['b_b_11'],
 #                               bind=roof_dropdown)

# Draw the chart
final = (heatmap + text).properties(
    height = 300,
    width = 800
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    tier_select
).transform_filter(
    tier_select 
# ).add_selection(
#     roof_select
# ).transform_filter(
#     roof_select
).properties(
    title={
      "text": ['Commonly Used Cooking Fuels and Stoves'], 
    #  "subtitle": ["You are viewing XX% of responses from the Kenya Multi-Tiered Framework Survey.", " "],
      "color": "black",
      "subtitleColor": "black"
    }
)

final

In [ ]:
# Step 1: create the scatterplot
# How much would you sell your land for?

df = module[module[['n_n_1b', 'n_n_1c', 'n_n_1b_unit']].notnull().all(1)]

# Filters
locality_options = [None, 'Urban', 'Rural']
locality_labels = ['National', 'Urban', 'Rural']
locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality_ur'],
    bind=locality_dropdown)

tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, labels = tier_labels, name = "Tiers  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# You need 2 unit filters to apply to both the scatterplot and histogram.
units = ['Acre', 'sq metres','Other']
unit_labels = ['Acre', 'Square meter','Other']
unit_dropdown=alt.binding_select(options=units, labels = unit_labels, name = "Units  ")
unit_select=alt.selection_single(fields=['n_n_1b_unit:N'],
                                bind=unit_dropdown)

units = [None, 'Acre', 'sq metres','Other']
unit_labels = ['All units', 'Acre', 'Square meter','Other']
unit_dropdown=alt.binding_select(options=units, labels = unit_labels, name = "Units  ")
unit_select=alt.selection_single(fields=['n_n_1b_unit'],
                                 bind=unit_dropdown)
 
# Scatterplot    
points = alt.Chart(df).mark_point().encode(
    x=alt.X('n_n_1b:Q',
           axis = alt.Axis(title = 'What is the total size of the land?'),
           scale = alt.Scale(domain=(1,100),clamp = True)),
    y=alt.Y('n_n_1c:Q',
            axis=alt.Axis(title='How much would you sell your land for?'),
           scale = alt.Scale(domain=(1,70000000),clamp = True)),
    color = alt.Color('n_n_1b_unit:N', legend = alt.Legend(title = "Units"))
)


scatterplot = (points).properties(
    height = 300,
    width = 500
).add_selection(brush)

scatterplot

In [ ]:
# Step 2: add the histogram
df = module[module[['n_n_1b']].notnull().all(1)]

points = alt.Chart(df).mark_point().encode(
    x=alt.X('n_n_1b:Q',
           axis = alt.Axis(title = 'What is the total size of the land?'),
           scale = alt.Scale(domain=(1,100),clamp = True)),
    y=alt.Y('n_n_1c:Q',
            axis=alt.Axis(title='How much would you sell your land for?'),
           scale = alt.Scale(domain=(1,70000000),clamp = True)),
    color = alt.Color('n_n_1b_unit:N', legend = alt.Legend(title = "Units"))
)

scatterplot = (points).properties(
    height = 300,
    width = 500
).add_selection(brush)

chart = alt.Chart(df).mark_bar(
).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).encode(
    alt.X("n_n_1b", 
          bin=alt.Bin(extent=[0, 100], step=5), 
          scale = alt.Scale(domain=(0,100),clamp = True),
         axis = alt.Axis(title = "Units of Land")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = "Percent"),
    tooltip = alt.Tooltip('sum(pct):Q', format = '.2%')
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20)
)

# Draw the chart
histogram = chart.properties(
    height = 300,
    width = 500,
    title = ''
).transform_filter(brush)


scatterplot & histogram

In [ ]:
# Finally, add filters

final = (scatterplot & histogram
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    tier_select
).transform_filter(
    tier_select 
).add_selection(
    unit_select
).transform_filter(
    unit_select
).properties(
    title={
      "text": ["Example (YOUR TITLE HERE) "], 
      "subtitle": ["You are viewing XX% of responses from the Kenya Multi-Tiered Framework Survey.", "Drag and drop a box over the scatterplot to filter the histogram, or use the dropdown filters below.", ""],
      "color": "black",
      "subtitleColor": "black"
    }
)

final

In [ ]:
# Save as an HTML file
final.save('final.html')

# Save as a JSON file
final.save('final.json')